In [12]:
# modified from https://github.com/SherlockLiao/Deep-Dream/blob/master/show_image.ipynb
import torch
import torchvision.models as models
from torchvision import transforms
from PIL import Image
from deepDream import dream
import torch.nn as nn
import spectroUtils as sUtils
import IPython.display as ipd
import librosa
import librosa.display
import numpy as np

In [13]:
#Original hip-hopaudio
trackId = 2
spectroSize = 224
#spectroSize = 300
#spectroSize = None
minAmp = -80.0
maxAmp = 1.9073486e-06
audioDirectory = "data/fma_small/"
audioFilename = audioDirectory + "000/000002.mp3"
x, sr = librosa.load(audioFilename, sr=None, mono=True, duration = 10, offset = 0)
start, end = 0, 30
ipd.Audio(data=x[start*sr:end*sr], rate=sr)

In [14]:
scaledSpectro, phase, origSpectroSize = sUtils.loadSpectro(trackId, spectroSize, minAmp, maxAmp)
scaledSpectro = scaledSpectro.data.numpy()
#scaledSpectro = scaledSpectro/255.0
print(scaledSpectro.shape)
scaledSpectro
print (np.angle(phase))

(1, 224, 224)
[[-3.14159250e+00  0.00000000e+00 -3.14159250e+00 ... -3.14159250e+00
  -3.14159250e+00 -3.14159250e+00]
 [ 3.14159250e+00  2.11385727e+00 -1.53498650e+00 ... -1.03498995e+00
  -1.21175036e-01  1.63016260e-01]
 [ 3.14159250e+00 -2.55471396e+00  2.46422008e-01 ...  2.07754421e+00
  -3.12831593e+00 -6.91219985e-01]
 ...
 [-3.14159250e+00  4.36230570e-01 -2.66553068e+00 ...  3.50956440e-01
  -2.13325405e+00  1.02496338e+00]
 [ 4.48949173e-13  1.84509587e+00  4.40762997e-01 ...  3.08023548e+00
  -9.98455524e-01 -2.62193227e+00]
 [ 0.00000000e+00 -3.14159250e+00 -3.14159250e+00 ... -3.14159250e+00
   0.00000000e+00  0.00000000e+00]]


In [15]:
# Get the power spectrogram from decibal version
backToSpectro = sUtils.unscaleSpectro(scaledSpectro[0], origSpectroSize, minAmp, maxAmp)
# Multiply power spectrogram with phase to get original complex spectrogram
backToSpectro = backToSpectro*phase

# Revert complex spectrogram to audio
n = len(x)
y_hat = librosa.istft(backToSpectro, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)

In [16]:
model = models.__dict__['resnet18']()
model = torch.nn.DataParallel(model)
model

DataParallel (
  (module): ResNet (
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
    (relu): ReLU (inplace)
    (maxpool): MaxPool2d (size=(3, 3), stride=(2, 2), padding=(1, 1), dilation=(1, 1))
    (layer1): Sequential (
      (0): BasicBlock (
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
        (relu): ReLU (inplace)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
      )
      (1): BasicBlock (
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
        (relu): ReLU (inplace)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride

In [17]:
checkpoint_path = 'resnet18/checkpoints/model_best.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
model.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))

=> loading checkpoint 'resnet18/checkpoints/model_best.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/model_best.pth.tar' (epoch: 57) (best_acc: 50.57766367627047)


In [18]:
dreamSpectro = dream(model, scaledSpectro)
dreamSpectro = dreamSpectro[0,:]
print ("dreamSpectro")
print (dreamSpectro)

model after removing 0
(1, 41, 41)
ratio 138.42328
learning_rate_use 0.004334531049720736
imgBefore [[[130.56349  184.52676  218.98064  ... 208.89153  201.4065   180.78021 ]
  [161.27505  190.06917  202.99565  ... 195.06941  200.89551  193.13019 ]
  [160.90948  186.78056  197.09256  ... 193.29453  197.95786  192.71089 ]
  ...
  [ 51.76121   59.960533  59.281235 ...  60.362057  59.750786 106.75565 ]
  [ 52.769333  58.88224   58.55359  ...  58.77784   59.439327 106.58739 ]
  [ 53.22973   62.109764  60.048416 ...  62.17708   59.98676  107.4638  ]]]
imgAfter (1, 41, 41)
ratio 139.02327
learning_rate_use 0.0043158242609040096
imgBefore [[[131.12698  185.32315  219.92572  ... 209.79306  202.27573  181.56042 ]
  [161.97108  190.88948  203.87175  ... 195.9113   201.76254  193.9637  ]
  [161.60394  187.58667  197.94318  ... 194.12875  198.81221  193.5426  ]
  ...
  [ 51.984604  60.21931   59.537083 ...  60.62257   60.00866  107.21639 ]
  [ 52.997078  59.136364  58.806297 ...  59.031513  59.6958

ratio 163.47958
learning_rate_use 0.0036701830667331976
imgBefore [[[153.64183  209.16481  212.09131  ... 233.3475   227.27707  212.73471 ]
  [199.69376  217.39154  225.27875  ... 230.0619   239.09683  237.20535 ]
  [171.0246   221.00964  221.86786  ... 232.72801  239.7409   218.00647 ]
  ...
  [ 61.973274  71.18072   69.443756 ...  67.35257   76.24455  125.42997 ]
  [ 60.56528   69.26944   68.72171  ...  71.63222   76.69493  125.633194]
  [ 62.638546  71.31981   73.06548  ...  68.18408   74.85461  126.4591  ]]]
imgAfter (1, 81, 81)
ratio 164.0776
learning_rate_use 0.0036568061534512724
imgBefore [[[154.20367  209.92969  212.86688  ... 234.2008   228.10818  213.51263 ]
  [200.424    218.1865   226.10255  ... 230.9032   239.97116  238.07277 ]
  [171.65     221.81784  222.67918  ... 233.57906  240.61758  218.80368 ]
  ...
  [ 62.199898  71.44101   69.6977   ...  67.59886   76.52336  125.88864 ]
  [ 60.786755  69.52274   68.973015 ...  71.894165  76.97539  126.09261 ]
  [ 62.867603  71.58

/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)



ratio 179.6945
learning_rate_use 0.0033390002886266577
imgBefore [[[168.81064  223.92494  235.84825  ... 253.90111  246.52577  233.73758 ]
  [225.77051  236.15991  245.69302  ... 255.85144  255.85144  253.82343 ]
  [207.35724  227.3131   246.62901  ... 255.85144  255.85144  255.85144 ]
  ...
  [ 68.99976   78.66036   69.64695  ...  75.07087   91.83918  138.40031 ]
  [ 64.93186   77.55804   75.52983  ...  83.59884   86.64166  137.80643 ]
  [ 68.82273   79.82299   75.88728  ...  81.25433   84.674255 138.94414 ]]]
imgAfter (1, 114, 114)
ratio 180.27347
learning_rate_use 0.0033282767930192317
imgBefore [[[169.37248  224.67023  236.63322  ... 254.74615  247.34628  234.51552 ]
  [226.52194  236.94592  246.51076  ... 255.84871  255.84871  254.66821 ]
  [208.04738  228.06966  247.44986  ... 255.84871  255.84871  255.84871 ]
  ...
  [ 69.229416  78.922165  69.87875  ...  75.320724  92.144844 138.86095 ]
  [ 65.14797   77.81617   75.78121  ...  83.877075  86.93003  138.26509 ]
  [ 69.05179   80

  [ 77.361755  88.056435  94.98249  ...  98.69356   96.605675 156.18338 ]]]
imgAfter (1, 224, 224)
ratio 197.91508
learning_rate_use 0.003031603177132712
imgBefore [[[190.33072  239.98111  253.84776  ... 255.77306  248.76668  255.77306 ]
  [240.26779  255.23843  255.77306  ... 255.77306  255.77306  254.33711 ]
  [255.77306  255.77306  255.77306  ... 255.77306  255.77306  255.77306 ]
  ...
  [ 77.02053   76.3795    89.69406  ... 102.32846   85.72384  155.40071 ]
  [ 64.75871   71.37421   98.002266 ... 101.19864   99.93063  155.48932 ]
  [ 77.59628   88.32339   95.27044  ...  98.99276   96.898544 156.65686 ]]]
imgAfter (1, 224, 224)
ratio 198.32942
learning_rate_use 0.0030252697454483737
imgBefore [[[190.90652  240.70712  254.61572  ... 255.77144  249.51926  255.77144 ]
  [240.99466  255.77144  255.77144  ... 255.77144  255.77144  255.10655 ]
  [255.77144  255.77144  255.77144  ... 255.77144  255.77144  255.77144 ]
  ...
  [ 77.25354   76.61057   89.96541  ... 102.63803   85.98318  155.8

In [19]:
#Convert it back to 
backToSpectro = sUtils.unscaleSpectro(dreamSpectro, origSpectroSize, minAmp, maxAmp)
# Multiply power spectrogram with phase to get original complex spectrogram
backToSpectro = backToSpectro*phase

# Revert complex spectrogram to audio
n = len(x)
y_hat = librosa.istft(backToSpectro, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)

## Control The Dream

In [31]:
spectroSize = 224
otherTrackId = 5158
otherSpectro, otherPhase, otherOrigSpectroSize = sUtils.loadSpectro(otherTrackId, spectroSize, minAmp, maxAmp)
otherSpectro = otherSpectro.data.numpy()
audioFilename = audioDirectory + "005/005158.mp3"
x, sr = librosa.load(audioFilename, sr=None, mono=True, duration = 10, offset = 0)
start, end = 0, 10
ipd.Audio(data=x[start*sr:end*sr], rate=sr)

In [32]:
model = models.__dict__['resnet18']()
model = torch.nn.DataParallel(model)
checkpoint_path = 'resnet18/checkpoints/model_best.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
model.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))
model = nn.Sequential(*list(model.children())[:-3])

=> loading checkpoint 'resnet18/checkpoints/model_best.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/model_best.pth.tar' (epoch: 57) (best_acc: 50.57766367627047)


In [33]:
control_features = model.forward(otherSpectro)

In [34]:
def objective_guide(dst, guide_features):
    x = dst.data[0].cpu().numpy().copy()
    #print ("guide_features", guide_features.shape)
    y = guide_features
    w, h = x.shape
    ch = 1
    x = x.reshape(ch,-1)
    y = y.reshape(ch,-1)
    A = x.T.dot(y) # compute the matrix of dot-products with guide features
    result = y[:,A.argmax(1)] # select ones that match best
    if torch.cuda.is_available():
        result = torch.Tensor(np.array([result.reshape(ch, w, h)], dtype=np.float)).cuda()
    else:
        result = torch.Tensor(np.array([result.reshape(ch, w, h)], dtype=np.float))
    return result

In [35]:
hopRockDreamSpectro = dream(model, scaledSpectro, control=control_features, distance=objective_guide, layerNumber=3)
print(hopRockDreamSpectro)

model after removing 0
(1, 41, 41)


/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)


ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[130.6      184.33038  218.63556  ... 208.59     201.13727  180.6     ]
  [161.17903  189.84886  202.71956  ... 194.82753  200.62848  192.89668 ]
  [160.81503  186.57446  196.84195  ... 193.0603   197.7035   192.47919 ]
  ...
  [ 52.137817  60.301754  59.625385 ...  60.70154   60.09291  106.89491 ]
  [ 53.141586  59.228115  58.90088  ...  59.124165  59.782795 106.72737 ]
  [ 53.6       62.441708  60.389256 ...  62.50873   60.327866 107.6     ]]]
imgAfter (1, 41, 41)


/home/iaakhter/cs532l/DreamingInMusic/deepDream.py:48: UserWarning: other is not broadcastable to self, but they have the same number of elements.  Falling back to deprecated pointwise behavior.
  img_variable.data.add_(img_variable.grad.data * learning_rate_use)


ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[131.20001  184.93039  219.23557  ... 209.19     201.73727  181.20001 ]
  [161.77904  190.44887  203.31956  ... 195.42754  201.22849  193.49669 ]
  [161.41504  187.17447  197.44196  ... 193.66031  198.30351  193.0792  ]
  ...
  [ 52.737816  60.901752  60.225384 ...  61.30154   60.69291  107.49491 ]
  [ 53.741585  59.828114  59.500877 ...  59.724163  60.382793 107.32737 ]
  [ 54.199997  63.041706  60.989254 ...  63.10873   60.927864 108.2     ]]]
imgAfter (1, 41, 41)
ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[131.80002  185.5304   219.83557  ... 209.79001  202.33728  181.80002 ]
  [162.37904  191.04887  203.91957  ... 196.02754  201.82849  194.0967  ]
  [162.01505  187.77448  198.04196  ... 194.26031  198.90352  193.6792  ]
  ...
  [ 53.337814  61.50175   60.825382 ...  61.90154   61.292908 108.09491 ]
  [ 54.341583  60.428112  60.100876 ...  60.32416   60.98279  107.92737 ]
  [ 54.799995  63.641705  61.

...

  [ 82.99992   90.73625   91.99393  ...  86.545715  90.706604 137.00003 ]]]
imgAfter (1, 81, 81)
ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[160.60031  210.39546  209.62706  ... 227.7149   223.25514  210.60031 ]
  [203.15918  216.85966  222.0647   ... 224.52975  234.23448  233.46706 ]
  [173.05585  219.59735  218.46825  ... 227.22266  234.59003  213.90756 ]
  ...
  [ 83.02761   91.46934   89.43359  ...  86.44      92.73031  136.71294 ]
  [ 81.642555  89.49449   88.593895 ...  90.615906  93.11071  136.86617 ]
  [ 83.59992   91.33625   92.593925 ...  87.14571   91.3066   137.60004 ]]]
imgAfter (1, 81, 81)
ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[161.20032  210.99547  210.22707  ... 228.31491  223.85515  211.20032 ]
  [203.75919  217.45967  222.6647   ... 225.12976  234.83449  234.06706 ]
  [173.65585  220.19736  219.06825  ... 227.82266  235.19003  214.50757 ]
  ...
  [ 83.62761   92.069336  90.03359  ...  87.04      93.33031  137.31294 ]
  [ 82

ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[170.20041  217.02176  224.23097  ... 236.07918  230.59163  220.20041 ]
  [220.83557  226.38658  232.3518   ... 240.71837  241.37468  237.40884 ]
  [201.25667  216.49745  232.40524  ... 237.8093   254.68481  251.12595 ]
  ...
  [ 93.57592  101.95398   92.69183  ...  95.08758  107.63891  146.8453  ]
  [ 89.604195 100.82446   98.26648  ... 103.321075 102.58002  146.20013 ]
  [ 93.1999   102.79722   98.28572  ... 101.17219  100.72013  147.20013 ]]]
imgAfter (1, 114, 114)
ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[170.80042  217.62177  224.83098  ... 236.67918  231.19164  220.80042 ]
  [221.43558  226.98659  232.95181  ... 241.31837  241.97469  238.00885 ]
  [201.85667  217.09746  233.00525  ... 238.4093   255.28482  251.72595 ]
  ...
  [ 94.17592  102.55398   93.29183  ...  95.68758  108.23891  147.44531 ]
  [ 90.20419  101.42446   98.86648  ... 103.921074 103.180016 146.80014 ]
  [ 93.7999   103.39722   9

ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[179.8005   224.02065  230.41058  ... 242.08981  238.88857  229.8005  ]
  [230.65585  241.83318  249.66847  ... 250.67421  253.67868  246.66843 ]
  [230.11496  216.5309   231.99353  ... 255.5427   240.22778  245.85054 ]
  ...
  [104.409935 110.72353  113.174545 ... 113.07091  111.89047  155.80023 ]
  [ 95.630066 105.7691   115.01782  ... 117.931435 108.01017  155.80023 ]
  [102.79987  114.21497  109.74956  ... 112.79991  108.61762  156.80023 ]]]
imgAfter (1, 160, 160)
ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[180.40051  224.62065  231.01059  ... 242.68982  239.48857  230.40051 ]
  [231.25586  242.43318  250.26848  ... 251.27422  254.27869  247.26843 ]
  [230.71497  217.1309   232.59354  ... 255.6      240.82779  246.45055 ]
  ...
  [105.00993  111.32353  113.77454  ... 113.670906 112.49047  156.40024 ]
  [ 96.230064 106.369095 115.61782  ... 118.53143  108.61017  156.40024 ]
  [103.39987  114.81497  11

ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[189.4006   233.62074  240.01068  ... 251.68991  248.48866  239.4006  ]
  [240.25595  251.43327  255.6      ... 255.6      255.6      255.6     ]
  [239.71506  226.131    241.59363  ... 255.6      249.82788  255.45064 ]
  ...
  [114.00991  120.32351  122.77452  ... 122.67088  121.49045  165.40033 ]
  [105.23004  115.36907  124.6178   ... 127.53141  117.610146 165.40033 ]
  [112.39985  123.81495  119.34953  ... 122.39989  118.2176   166.40033 ]]]
imgAfter (1, 160, 160)
ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[190.00061  234.22075  240.61069  ... 252.28992  249.08867  240.00061 ]
  [240.85596  252.03328  255.6      ... 255.6      255.6      255.6     ]
  [240.31506  226.731    242.19363  ... 255.6      250.42789  255.6     ]
  ...
  [114.60991  120.92351  123.37452  ... 123.27088  122.09045  166.00034 ]
  [105.83004  115.96907  125.2178   ... 128.13141  118.210144 166.00034 ]
  [112.99985  124.41495  11

ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[199.0007   240.00072  248.00072  ... 255.6      244.0007   249.0007  ]
  [241.0007   255.0007   255.6      ... 255.6      255.6      253.66843 ]
  [255.6      255.6      255.6      ... 255.6      255.6      255.6     ]
  ...
  [121.999825 119.999825 131.99988  ... 135.00002  114.00006  175.00043 ]
  [109.999825 114.999825 139.99994  ... 134.       128.00006  175.00043 ]
  [121.999825 130.99986  136.99994  ... 131.99997  125.00006  176.00043 ]]]
imgAfter (1, 224, 224)
ratio 251.0
learning_rate_use 0.002390438247011952
imgBefore [[[199.60071 240.60072 248.60072 ... 255.6     244.60071 249.60071]
  [241.60071 255.6     255.6     ... 255.6     255.6     254.26843]
  [255.6     255.6     255.6     ... 255.6     255.6     255.6    ]
  ...
  [122.59982 120.59982 132.59988 ... 135.60002 114.60006 175.60043]
  [110.59982 115.59982 140.59995 ... 134.6     128.60007 175.60043]
  [122.59982 131.59987 137.59995 ... 132.59998 125.60006 

In [36]:
hopRockDreamSpectro = hopRockDreamSpectro[0,:]
#Convert it back to 
backToSpectro = sUtils.unscaleSpectro(hopRockDreamSpectro, origSpectroSize, minAmp, maxAmp)
# Multiply power spectrogram with phase to get original complex spectrogram
backToSpectro = backToSpectro*phase

# Revert complex spectrogram to audio
n = len(x)
y_hat = librosa.istft(backToSpectro, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)